In [1]:
from common import *

In [2]:
fnames = glob('../data/lingvo/raw/*')

In [3]:
dim = 300

In [4]:
import gc, io

prog = re.compile("[\W\d]", re.UNICODE)

def process(fnames, i):
    with io.open('../data/lingvo/%s.txt'%i, 'w', encoding='utf8') as fw:
        for fn in fnames:
            with io.open(fn, encoding='utf8') as fr:
                text = fr.read()
            sents = sent_tokenize(text)
            sents = [[w for w in s.split() if w not in stop_list and len(w)>1] 
                     for s in sents]
            sents = [s for s in sents if len(s)]
            s = json.dumps((basename(fn).split('.')[0], sents))            
            fw.write(s + u'\n')
    gc.collect()


In [10]:
parallelizer = Parallel(n_jobs=cpu_count-1)

tasks_iterator = ( delayed(process)(list_block, i) for 
                  i, list_block in enumerate(grouper(len(fnames)//500, fnames)) ) 
result = parallelizer( tasks_iterator )

In [ ]:
pwd = !pwd
%cd ../data/lingvo/
!cat *.txt > corpus_json.txt&&gzip -f corpus_json.txt&&rm *.txt
%cd {pwd[0]}

^C
/notebooks/pat


In [5]:
import ujson

def iter_docs():
    with GzipFile('../data/lingvo/corpus_json.txt.gz', 'r') as fr:
        for line in fr:
            _id, sents = ujson.loads(line)
            yield _id, sents
    
def iter_sents():
    for _id, sents in iter_docs():
        for s in sents:
            yield s
                
class Sentences(object):
    def __iter__(self):
        for sent in iter_sents():
            yield sent
            
class Documents(object):
    def __iter__(self):
        for _id, doc in iter_docs():
            unlisted = [w for s in doc for w in s]
            yield gensim.models.doc2vec.TaggedDocument(unlisted, [_id])

In [13]:
bigram = gensim.models.Phrases(iter_sents())

2017-10-23 14:15:51,409 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-23 14:15:51,413 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words and 0 word types
2017-10-23 14:15:51,685 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 123763 words and 68811 word types
2017-10-23 14:15:51,924 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 247232 words and 126750 word types
2017-10-23 14:15:52,157 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 361814 words and 181905 word types
2017-10-23 14:15:52,417 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 476326 words and 236790 word types
2017-10-23 14:15:52,631 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 582163 words and 284932 word types
2017-10-23 14:15:52,877 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 707456 words and 338864 word types
2017-10-23 14:15:53,148 [MainThread  ] [INFO ]  PROGRESS: at sentenc

2017-10-23 14:16:07,146 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 7567876 words and 2647655 word types
2017-10-23 14:16:07,375 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7682367 words and 2681041 word types
2017-10-23 14:16:07,620 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7807102 words and 2711419 word types
2017-10-23 14:16:07,872 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7928153 words and 2745114 word types
2017-10-23 14:16:08,134 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 8055747 words and 2778601 word types
2017-10-23 14:16:08,493 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 8174804 words and 2811945 word types
2017-10-23 14:16:08,720 [MainThread  ] [INFO ]  PROGRESS: at sentence #710000, processed 8289637 words and 2843494 word types
2017-10-23 14:16:08,960 [MainThread  ] [INFO ]  PROGRESS: at sentence #720000, processed 8407980 words and 2876660 wor

2017-10-23 14:16:22,820 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 15124310 words and 4663688 word types
2017-10-23 14:16:23,073 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 15239642 words and 4693827 word types
2017-10-23 14:16:23,314 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 15354120 words and 4723914 word types
2017-10-23 14:16:23,563 [MainThread  ] [INFO ]  PROGRESS: at sentence #1330000, processed 15475762 words and 4753731 word types
2017-10-23 14:16:23,792 [MainThread  ] [INFO ]  PROGRESS: at sentence #1340000, processed 15589302 words and 4782687 word types
2017-10-23 14:16:24,023 [MainThread  ] [INFO ]  PROGRESS: at sentence #1350000, processed 15699310 words and 4810258 word types
2017-10-23 14:16:24,266 [MainThread  ] [INFO ]  PROGRESS: at sentence #1360000, processed 15816553 words and 4845228 word types
2017-10-23 14:16:24,517 [MainThread  ] [INFO ]  PROGRESS: at sentence #1370000, processed 15935536 words

2017-10-23 14:16:38,513 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 22633648 words and 6459857 word types
2017-10-23 14:16:38,743 [MainThread  ] [INFO ]  PROGRESS: at sentence #1960000, processed 22746937 words and 6487341 word types
2017-10-23 14:16:38,985 [MainThread  ] [INFO ]  PROGRESS: at sentence #1970000, processed 22866400 words and 6514215 word types
2017-10-23 14:16:39,223 [MainThread  ] [INFO ]  PROGRESS: at sentence #1980000, processed 22986199 words and 6542427 word types
2017-10-23 14:16:39,463 [MainThread  ] [INFO ]  PROGRESS: at sentence #1990000, processed 23102422 words and 6566742 word types
2017-10-23 14:16:39,702 [MainThread  ] [INFO ]  PROGRESS: at sentence #2000000, processed 23221602 words and 6590987 word types
2017-10-23 14:16:39,933 [MainThread  ] [INFO ]  PROGRESS: at sentence #2010000, processed 23334692 words and 6618638 word types
2017-10-23 14:16:40,170 [MainThread  ] [INFO ]  PROGRESS: at sentence #2020000, processed 23448025 words

2017-10-23 14:16:53,847 [MainThread  ] [INFO ]  PROGRESS: at sentence #2600000, processed 30171468 words and 8115170 word types
2017-10-23 14:16:54,081 [MainThread  ] [INFO ]  PROGRESS: at sentence #2610000, processed 30282077 words and 8141265 word types
2017-10-23 14:16:54,329 [MainThread  ] [INFO ]  PROGRESS: at sentence #2620000, processed 30407113 words and 8165944 word types
2017-10-23 14:16:54,576 [MainThread  ] [INFO ]  PROGRESS: at sentence #2630000, processed 30526852 words and 8189657 word types
2017-10-23 14:16:54,825 [MainThread  ] [INFO ]  PROGRESS: at sentence #2640000, processed 30648527 words and 8211262 word types
2017-10-23 14:16:55,065 [MainThread  ] [INFO ]  PROGRESS: at sentence #2650000, processed 30765897 words and 8235159 word types
2017-10-23 14:16:55,294 [MainThread  ] [INFO ]  PROGRESS: at sentence #2660000, processed 30878939 words and 8258875 word types
2017-10-23 14:16:55,527 [MainThread  ] [INFO ]  PROGRESS: at sentence #2670000, processed 30993622 words

...

2017-10-23 14:56:47,152 [MainThread  ] [INFO ]  PROGRESS: at sentence #90870000, processed 1058545050 words and 36862350 word types
2017-10-23 14:56:47,386 [MainThread  ] [INFO ]  PROGRESS: at sentence #90880000, processed 1058658537 words and 36874084 word types
2017-10-23 14:56:47,632 [MainThread  ] [INFO ]  PROGRESS: at sentence #90890000, processed 1058775527 words and 36888655 word types
2017-10-23 14:56:47,881 [MainThread  ] [INFO ]  PROGRESS: at sentence #90900000, processed 1058895184 words and 36901436 word types
2017-10-23 14:56:48,131 [MainThread  ] [INFO ]  PROGRESS: at sentence #90910000, processed 1059012831 words and 36914165 word types
2017-10-23 14:56:48,380 [MainThread  ] [INFO ]  PROGRESS: at sentence #90920000, processed 1059132328 words and 36925697 word types
2017-10-23 14:56:48,633 [MainThread  ] [INFO ]  PROGRESS: at sentence #90930000, processed 1059254996 words and 36937568 word types
2017-10-23 14:56:48,867 [MainThread  ] [INFO ]  PROGRESS: at sentence #90940

2017-10-23 14:57:07,769 [MainThread  ] [INFO ]  PROGRESS: at sentence #91500000, processed 1065909505 words and 37644158 word types
2017-10-23 14:57:07,996 [MainThread  ] [INFO ]  PROGRESS: at sentence #91510000, processed 1066018471 words and 37654835 word types
2017-10-23 14:57:08,234 [MainThread  ] [INFO ]  PROGRESS: at sentence #91520000, processed 1066130600 words and 37667819 word types
2017-10-23 14:57:08,491 [MainThread  ] [INFO ]  PROGRESS: at sentence #91530000, processed 1066252773 words and 37681845 word types
2017-10-23 14:57:08,734 [MainThread  ] [INFO ]  PROGRESS: at sentence #91540000, processed 1066370642 words and 37691721 word types
2017-10-23 14:57:08,976 [MainThread  ] [INFO ]  PROGRESS: at sentence #91550000, processed 1066486380 words and 37703303 word types
2017-10-23 14:57:09,225 [MainThread  ] [INFO ]  PROGRESS: at sentence #91560000, processed 1066605370 words and 37717290 word types
2017-10-23 14:57:09,480 [MainThread  ] [INFO ]  PROGRESS: at sentence #91570

2017-10-23 14:57:23,156 [MainThread  ] [INFO ]  PROGRESS: at sentence #92130000, processed 1073250959 words and 38439765 word types
2017-10-23 14:57:23,383 [MainThread  ] [INFO ]  PROGRESS: at sentence #92140000, processed 1073358454 words and 38454401 word types
2017-10-23 14:57:23,620 [MainThread  ] [INFO ]  PROGRESS: at sentence #92150000, processed 1073471247 words and 38466534 word types
2017-10-23 14:57:23,885 [MainThread  ] [INFO ]  PROGRESS: at sentence #92160000, processed 1073597092 words and 38481513 word types
2017-10-23 14:57:24,135 [MainThread  ] [INFO ]  PROGRESS: at sentence #92170000, processed 1073713659 words and 38495953 word types
2017-10-23 14:57:24,390 [MainThread  ] [INFO ]  PROGRESS: at sentence #92180000, processed 1073835590 words and 38510523 word types
2017-10-23 14:57:24,642 [MainThread  ] [INFO ]  PROGRESS: at sentence #92190000, processed 1073947638 words and 38523705 word types
2017-10-23 14:57:24,906 [MainThread  ] [INFO ]  PROGRESS: at sentence #92200

2017-10-23 14:57:38,847 [MainThread  ] [INFO ]  PROGRESS: at sentence #92760000, processed 1080640918 words and 39225415 word types
2017-10-23 14:57:39,111 [MainThread  ] [INFO ]  PROGRESS: at sentence #92770000, processed 1080769097 words and 39237535 word types
2017-10-23 14:57:39,355 [MainThread  ] [INFO ]  PROGRESS: at sentence #92780000, processed 1080878098 words and 39250326 word types
2017-10-23 14:57:39,613 [MainThread  ] [INFO ]  PROGRESS: at sentence #92790000, processed 1080994216 words and 39264151 word types
2017-10-23 14:57:39,865 [MainThread  ] [INFO ]  PROGRESS: at sentence #92800000, processed 1081109654 words and 39271008 word types
2017-10-23 14:57:40,121 [MainThread  ] [INFO ]  PROGRESS: at sentence #92810000, processed 1081224528 words and 39285659 word types
2017-10-23 14:57:40,372 [MainThread  ] [INFO ]  PROGRESS: at sentence #92820000, processed 1081340810 words and 39296199 word types
2017-10-23 14:57:40,618 [MainThread  ] [INFO ]  PROGRESS: at sentence #92830

2017-10-23 14:57:54,509 [MainThread  ] [INFO ]  PROGRESS: at sentence #93390000, processed 1087979472 words and 39992440 word types
2017-10-23 14:58:21,108 [MainThread  ] [INFO ]  pruned out 26284200 tokens with count <=6 (before 40000001, after 13715801)
2017-10-23 14:58:21,177 [MainThread  ] [INFO ]  PROGRESS: at sentence #93400000, processed 1088096873 words and 13718795 word types
2017-10-23 14:58:21,426 [MainThread  ] [INFO ]  PROGRESS: at sentence #93410000, processed 1088210900 words and 13736213 word types
2017-10-23 14:58:21,685 [MainThread  ] [INFO ]  PROGRESS: at sentence #93420000, processed 1088328342 words and 13756425 word types
2017-10-23 14:58:21,949 [MainThread  ] [INFO ]  PROGRESS: at sentence #93430000, processed 1088454650 words and 13772053 word types
2017-10-23 14:58:22,211 [MainThread  ] [INFO ]  PROGRESS: at sentence #93440000, processed 1088580262 words and 13787336 word types
2017-10-23 14:58:22,470 [MainThread  ] [INFO ]  PROGRESS: at sentence #93450000, pro

In [14]:
bigram.save('../data/lingvo/bigram')

2017-10-23 14:58:34,251 [MainThread  ] [INFO ]  saving Phrases object under ../data/lingvo/bigram, separately None
2017-10-23 14:58:52,822 [MainThread  ] [INFO ]  saved ../data/lingvo/bigram


In [15]:
len(bigram.vocab)

14557616

In [16]:
len(bigram.vocab)

14557616

In [17]:
for phrase, score in bigram.export_phrases(islice(iter_sents(), 1000)):
    print('{0}   {1}'.format(phrase, score))

суперсплав никель   21.3022606177
суперсплав никель   21.3022606177
суперсплав никель   21.3022606177
карбид тантал   13.7427535397
суперсплав никель   21.3022606177
карбид тантал   13.7427535397
молибден вольфрам   23.2113732761
суперсплав никель   21.3022606177
молибден вольфрам   23.2113732761
карбид тантал   13.7427535397
суперсплав никель   21.3022606177
патент сша   11.7227021811
торговый наименование   46.1854482212
mo ta   11.2794752825
кристаллографический ориентация   16.039110751
mo ta   11.2794752825
ti zr   54.402871756
et al   40.2209213278
advance materials   39.3792914258
gas turbine   1476.03880694
advanced materials   234.215248558
cr мо   10.3330782714
hf nb   19.83279486
патент сша   11.7227021811
cr мо   10.3330782714
суперсплав суперсплав   38.3011743359
патент сша   11.7227021811
суперсплав никель   21.3022606177
карбид тантал   13.7427535397
цирконий гафний   40.9307139425
патент сша   11.7227021811
цирконий гафний   40.9307139425
карбид тантал   13.7427535397
д

In [31]:
bigram = gensim.models.phrases.Phrases.load('../data/lingvo/bigram_5_100')

2017-10-09 21:37:51,276 [MainThread  ] [INFO ]  loading Phrases object from ../data/lingvo/bigram_5_100
2017-10-09 21:38:17,725 [MainThread  ] [INFO ]  loaded ../data/lingvo/bigram_5_100


In [18]:
bigram_ph = gensim.models.phrases.Phraser(bigram)

2017-10-23 19:25:31,800 [MainThread  ] [INFO ]  source_vocab length 14557616
2017-10-23 19:25:39,470 [MainThread  ] [INFO ]  Phraser added 50000 phrasegrams
2017-10-23 19:25:46,912 [MainThread  ] [INFO ]  Phraser added 100000 phrasegrams
2017-10-23 19:25:54,396 [MainThread  ] [INFO ]  Phraser added 150000 phrasegrams
2017-10-23 19:26:02,070 [MainThread  ] [INFO ]  Phraser added 200000 phrasegrams
2017-10-23 19:26:09,498 [MainThread  ] [INFO ]  Phraser added 250000 phrasegrams
2017-10-23 19:26:17,145 [MainThread  ] [INFO ]  Phraser added 300000 phrasegrams
2017-10-23 19:26:24,717 [MainThread  ] [INFO ]  Phraser added 350000 phrasegrams
2017-10-23 19:26:32,147 [MainThread  ] [INFO ]  Phraser added 400000 phrasegrams
2017-10-23 19:26:39,652 [MainThread  ] [INFO ]  Phraser added 450000 phrasegrams
2017-10-23 19:26:47,341 [MainThread  ] [INFO ]  Phraser added 500000 phrasegrams
2017-10-23 19:26:54,853 [MainThread  ] [INFO ]  Phraser added 550000 phrasegrams
2017-10-23 19:27:02,590 [MainThre

In [19]:
bigram_ph.save('../data/lingvo/bigram_ph')

2017-10-23 19:28:25,907 [MainThread  ] [INFO ]  saving Phraser object under ../data/lingvo/bigram_ph, separately None
2017-10-23 19:28:27,291 [MainThread  ] [INFO ]  saved ../data/lingvo/bigram_ph


In [6]:
bigram_ph = gensim.models.phrases.Phraser.load('../data/lingvo/bigram_ph')

2017-10-25 11:33:23,411 [MainThread  ] [INFO ]  loading Phraser object from ../data/lingvo/bigram_ph
2017-10-25 11:33:24,051 [MainThread  ] [INFO ]  loaded ../data/lingvo/bigram_ph


In [8]:
trigram = gensim.models.Phrases(bigram_ph[iter_sents()], min_count=20, threshold=30)

2017-10-25 11:01:29,107 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-25 11:01:29,109 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words and 0 word types
2017-10-25 11:01:29,864 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 118553 words and 68121 word types
2017-10-25 11:01:30,573 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 235869 words and 126101 word types
2017-10-25 11:01:31,246 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 343029 words and 181214 word types
2017-10-25 11:01:31,912 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 451750 words and 236338 word types
2017-10-25 11:01:32,546 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 552966 words and 284694 word types
2017-10-25 11:01:33,264 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 670596 words and 339177 word types
2017-10-25 11:01:34,017 [MainThread  ] [INFO ]  PROGRESS: at sentenc

2017-10-25 11:02:13,869 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 7164852 words and 2712678 word types
2017-10-25 11:02:14,538 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7272406 words and 2747504 word types
2017-10-25 11:02:15,252 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7388612 words and 2779107 word types
2017-10-25 11:02:16,065 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7504693 words and 2814166 word types
2017-10-25 11:02:16,792 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 7624699 words and 2849023 word types
2017-10-25 11:02:17,484 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 7737573 words and 2883726 word types
2017-10-25 11:02:18,158 [MainThread  ] [INFO ]  PROGRESS: at sentence #710000, processed 7847371 words and 2916584 word types
2017-10-25 11:02:18,856 [MainThread  ] [INFO ]  PROGRESS: at sentence #720000, processed 7960162 words and 2951226 wor

2017-10-25 11:02:58,250 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 14311466 words and 4824743 word types
2017-10-25 11:02:58,922 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 14419712 words and 4856417 word types
2017-10-25 11:02:59,588 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 14526127 words and 4888183 word types
2017-10-25 11:03:00,296 [MainThread  ] [INFO ]  PROGRESS: at sentence #1330000, processed 14641867 words and 4919730 word types
2017-10-25 11:03:00,969 [MainThread  ] [INFO ]  PROGRESS: at sentence #1340000, processed 14750230 words and 4950185 word types
2017-10-25 11:03:01,618 [MainThread  ] [INFO ]  PROGRESS: at sentence #1350000, processed 14854922 words and 4979157 word types
2017-10-25 11:03:02,306 [MainThread  ] [INFO ]  PROGRESS: at sentence #1360000, processed 14965748 words and 5015777 word types
2017-10-25 11:03:03,000 [MainThread  ] [INFO ]  PROGRESS: at sentence #1370000, processed 15077258 words

2017-10-25 11:03:42,728 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 21416705 words and 6723052 word types
2017-10-25 11:03:43,391 [MainThread  ] [INFO ]  PROGRESS: at sentence #1960000, processed 21523453 words and 6752320 word types
2017-10-25 11:03:44,093 [MainThread  ] [INFO ]  PROGRESS: at sentence #1970000, processed 21637078 words and 6780640 word types
2017-10-25 11:03:44,804 [MainThread  ] [INFO ]  PROGRESS: at sentence #1980000, processed 21749971 words and 6810857 word types
2017-10-25 11:03:45,481 [MainThread  ] [INFO ]  PROGRESS: at sentence #1990000, processed 21860016 words and 6836759 word types
2017-10-25 11:03:46,176 [MainThread  ] [INFO ]  PROGRESS: at sentence #2000000, processed 21973909 words and 6862350 word types
2017-10-25 11:03:46,840 [MainThread  ] [INFO ]  PROGRESS: at sentence #2010000, processed 22081375 words and 6891477 word types
2017-10-25 11:03:47,514 [MainThread  ] [INFO ]  PROGRESS: at sentence #2020000, processed 22188520 words

2017-10-25 11:04:27,148 [MainThread  ] [INFO ]  PROGRESS: at sentence #2600000, processed 28554432 words and 8482037 word types
2017-10-25 11:04:27,811 [MainThread  ] [INFO ]  PROGRESS: at sentence #2610000, processed 28659117 words and 8509858 word types
2017-10-25 11:04:28,551 [MainThread  ] [INFO ]  PROGRESS: at sentence #2620000, processed 28776466 words and 8536132 word types
2017-10-25 11:04:29,248 [MainThread  ] [INFO ]  PROGRESS: at sentence #2630000, processed 28890522 words and 8561415 word types
2017-10-25 11:04:29,943 [MainThread  ] [INFO ]  PROGRESS: at sentence #2640000, processed 29002254 words and 8584485 word types
2017-10-25 11:04:30,647 [MainThread  ] [INFO ]  PROGRESS: at sentence #2650000, processed 29112086 words and 8610442 word types
2017-10-25 11:04:31,316 [MainThread  ] [INFO ]  PROGRESS: at sentence #2660000, processed 29219634 words and 8635771 word types
2017-10-25 11:04:31,984 [MainThread  ] [INFO ]  PROGRESS: at sentence #2670000, processed 29328641 words

...

2017-10-25 11:25:49,530 [MainThread  ] [INFO ]  PROGRESS: at sentence #20330000, processed 223850802 words and 16981732 word types
2017-10-25 11:25:50,171 [MainThread  ] [INFO ]  PROGRESS: at sentence #20340000, processed 223953441 words and 17000575 word types
2017-10-25 11:25:50,850 [MainThread  ] [INFO ]  PROGRESS: at sentence #20350000, processed 224060959 words and 17018012 word types
2017-10-25 11:25:51,574 [MainThread  ] [INFO ]  PROGRESS: at sentence #20360000, processed 224175881 words and 17036326 word types
2017-10-25 11:25:52,287 [MainThread  ] [INFO ]  PROGRESS: at sentence #20370000, processed 224287083 words and 17054539 word types
2017-10-25 11:25:52,963 [MainThread  ] [INFO ]  PROGRESS: at sentence #20380000, processed 224395226 words and 17072329 word types
2017-10-25 11:25:53,712 [MainThread  ] [INFO ]  PROGRESS: at sentence #20390000, processed 224512479 words and 17092529 word types
2017-10-25 11:25:54,420 [MainThread  ] [INFO ]  PROGRESS: at sentence #20400000, pr

2017-10-25 11:26:33,140 [MainThread  ] [INFO ]  PROGRESS: at sentence #20960000, processed 230813065 words and 18120334 word types
2017-10-25 11:26:33,838 [MainThread  ] [INFO ]  PROGRESS: at sentence #20970000, processed 230924275 words and 18139215 word types
2017-10-25 11:26:34,523 [MainThread  ] [INFO ]  PROGRESS: at sentence #20980000, processed 231034405 words and 18157294 word types
2017-10-25 11:26:35,179 [MainThread  ] [INFO ]  PROGRESS: at sentence #20990000, processed 231140092 words and 18174983 word types
2017-10-25 11:26:35,870 [MainThread  ] [INFO ]  PROGRESS: at sentence #21000000, processed 231251894 words and 18192807 word types
2017-10-25 11:26:36,567 [MainThread  ] [INFO ]  PROGRESS: at sentence #21010000, processed 231364916 words and 18209496 word types
2017-10-25 11:26:37,217 [MainThread  ] [INFO ]  PROGRESS: at sentence #21020000, processed 231467626 words and 18225039 word types
2017-10-25 11:26:37,931 [MainThread  ] [INFO ]  PROGRESS: at sentence #21030000, pr

2017-10-25 11:27:16,679 [MainThread  ] [INFO ]  PROGRESS: at sentence #21590000, processed 237750939 words and 19255736 word types
2017-10-25 11:27:17,361 [MainThread  ] [INFO ]  PROGRESS: at sentence #21600000, processed 237861869 words and 19275560 word types
2017-10-25 11:27:17,904 [MainThread  ] [INFO ]  PROGRESS: at sentence #21610000, processed 237946647 words and 19290646 word types
2017-10-25 11:27:18,605 [MainThread  ] [INFO ]  PROGRESS: at sentence #21620000, processed 238055001 words and 19308880 word types
2017-10-25 11:27:19,336 [MainThread  ] [INFO ]  PROGRESS: at sentence #21630000, processed 238165183 words and 19324801 word types
2017-10-25 11:27:20,093 [MainThread  ] [INFO ]  PROGRESS: at sentence #21640000, processed 238281690 words and 19342440 word types
2017-10-25 11:27:20,835 [MainThread  ] [INFO ]  PROGRESS: at sentence #21650000, processed 238392567 words and 19362537 word types
2017-10-25 11:27:21,537 [MainThread  ] [INFO ]  PROGRESS: at sentence #21660000, pr

2017-10-25 11:28:00,395 [MainThread  ] [INFO ]  PROGRESS: at sentence #22220000, processed 244662311 words and 20367441 word types
2017-10-25 11:28:01,098 [MainThread  ] [INFO ]  PROGRESS: at sentence #22230000, processed 244774986 words and 20384844 word types
2017-10-25 11:28:01,737 [MainThread  ] [INFO ]  PROGRESS: at sentence #22240000, processed 244875076 words and 20401416 word types
2017-10-25 11:28:02,443 [MainThread  ] [INFO ]  PROGRESS: at sentence #22250000, processed 244990561 words and 20417924 word types
2017-10-25 11:28:03,155 [MainThread  ] [INFO ]  PROGRESS: at sentence #22260000, processed 245105585 words and 20437326 word types
2017-10-25 11:28:03,840 [MainThread  ] [INFO ]  PROGRESS: at sentence #22270000, processed 245217581 words and 20455153 word types
2017-10-25 11:28:04,547 [MainThread  ] [INFO ]  PROGRESS: at sentence #22280000, processed 245330924 words and 20475548 word types
2017-10-25 11:28:05,224 [MainThread  ] [INFO ]  PROGRESS: at sentence #22290000, pr

KeyboardInterrupt: 

In [ ]:
trigram.save('../data/lingvo/trigram_20_30')

In [7]:
trigram = gensim.models.phrases.Phrases.load(join(DATA_FOLDER, '../data/lingvo/trigram'))

2017-10-25 11:31:39,851 [MainThread  ] [INFO ]  loading Phrases object from ../data/../data/lingvo/trigram
2017-10-25 11:31:55,374 [MainThread  ] [INFO ]  loaded ../data/../data/lingvo/trigram


In [11]:
for s in islice(trigram[bigram_ph[iter_sents()]], 1000):
    for w in s:
        if len(w.split('_')) > 2:
            print(w)

суперсплав_никель_направленно
суперсплав_никель_направленно
суперсплав_никель_направленно
кобальт_молибден_вольфрам
суперсплав_никель_направленно
кобальт_молибден_вольфрам
суперсплав_никель_направленно
mo_ta_nb
al_ti_zr
advanced_materials_process
cr_мо_ti
cr_мо_ti
затруднять_делать_невозможный
astm_american_society
test_materials_американский_общество
детектирование_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
среднеквадратичный_rm_демодулировать
rm_rmslev_подсинхронный_резонанс
rm_rmslev_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
среднеквадратичный_rm_демодулировать
rm_rmslev_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
явление_подсинхронный_резонанс
явление_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
явление_подсинхронный_резонанс
детектирование_подсинхронный_резонанс
среднеквадратичный_rm_демодулировать
r

In [40]:
trigram_ph = gensim.models.phrases.Phraser(trigram)
trigram_ph.save('../data/lingvo/trigram_ph')

2017-10-24 09:12:01,557 [MainThread  ] [INFO ]  source_vocab length 29961985
2017-10-24 09:12:08,168 [MainThread  ] [INFO ]  Phraser added 50000 phrasegrams
2017-10-24 09:12:14,629 [MainThread  ] [INFO ]  Phraser added 100000 phrasegrams
2017-10-24 09:12:21,170 [MainThread  ] [INFO ]  Phraser added 150000 phrasegrams
2017-10-24 09:12:27,652 [MainThread  ] [INFO ]  Phraser added 200000 phrasegrams
2017-10-24 09:12:34,117 [MainThread  ] [INFO ]  Phraser added 250000 phrasegrams
2017-10-24 09:12:40,637 [MainThread  ] [INFO ]  Phraser added 300000 phrasegrams
2017-10-24 09:12:47,126 [MainThread  ] [INFO ]  Phraser added 350000 phrasegrams
2017-10-24 09:12:53,535 [MainThread  ] [INFO ]  Phraser added 400000 phrasegrams
2017-10-24 09:12:59,984 [MainThread  ] [INFO ]  Phraser added 450000 phrasegrams
2017-10-24 09:13:06,406 [MainThread  ] [INFO ]  Phraser added 500000 phrasegrams
2017-10-24 09:13:13,090 [MainThread  ] [INFO ]  Phraser added 550000 phrasegrams
2017-10-24 09:13:20,010 [MainThre

In [6]:
trigram_ph = gensim.models.phrases.Phrases.load('../data/lingvo/trigram_ph')

2017-10-25 10:22:59,258 [MainThread  ] [INFO ]  loading Phrases object from ../data/lingvo/trigram_ph
2017-10-25 10:23:01,073 [MainThread  ] [INFO ]  loaded ../data/lingvo/trigram_ph


In [ ]:
model = Word2Vec(Sentences(), size=dim, sg=1, min_count=10, window=10, workers=8)

2017-10-13 12:05:54,498 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-13 12:05:54,513 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2017-10-13 12:05:54,675 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 108194 words, keeping 11923 word types
2017-10-13 12:05:54,856 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 215695 words, keeping 18597 word types
2017-10-13 12:05:54,990 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 333525 words, keeping 25805 word types
2017-10-13 12:05:55,139 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 456196 words, keeping 32259 word types
2017-10-13 12:05:55,294 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 580554 words, keeping 37391 word types
2017-10-13 12:05:55,436 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 695913 words, keeping 41846 word types
2017-10-13 12:05:55,582 [MainThread  ]

2017-10-13 12:06:03,189 [MainThread  ] [INFO ]  PROGRESS: at sentence #630000, processed 6912698 words, keeping 212405 word types
2017-10-13 12:06:03,334 [MainThread  ] [INFO ]  PROGRESS: at sentence #640000, processed 7029422 words, keeping 214492 word types
2017-10-13 12:06:03,479 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 7143134 words, keeping 216730 word types
2017-10-13 12:06:03,616 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7252544 words, keeping 219287 word types
2017-10-13 12:06:03,764 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7369004 words, keeping 221799 word types
2017-10-13 12:06:03,894 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7474811 words, keeping 223765 word types
2017-10-13 12:06:04,030 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 7585323 words, keeping 226257 word types
2017-10-13 12:06:04,174 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 7

2017-10-13 12:06:11,826 [MainThread  ] [INFO ]  PROGRESS: at sentence #1260000, processed 13775627 words, keeping 347112 word types
2017-10-13 12:06:11,961 [MainThread  ] [INFO ]  PROGRESS: at sentence #1270000, processed 13881680 words, keeping 349401 word types
2017-10-13 12:06:12,138 [MainThread  ] [INFO ]  PROGRESS: at sentence #1280000, processed 13998165 words, keeping 352595 word types
2017-10-13 12:06:12,261 [MainThread  ] [INFO ]  PROGRESS: at sentence #1290000, processed 14097940 words, keeping 354205 word types
2017-10-13 12:06:12,403 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 14211202 words, keeping 355867 word types
2017-10-13 12:06:12,546 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 14321740 words, keeping 357628 word types
2017-10-13 12:06:12,685 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 14427613 words, keeping 358908 word types
2017-10-13 12:06:12,833 [MainThread  ] [INFO ]  PROGRESS: at sentence #13300

2017-10-13 12:06:21,036 [MainThread  ] [INFO ]  PROGRESS: at sentence #1890000, processed 20776871 words, keeping 468625 word types
2017-10-13 12:06:21,159 [MainThread  ] [INFO ]  PROGRESS: at sentence #1900000, processed 20888023 words, keeping 470846 word types
2017-10-13 12:06:21,293 [MainThread  ] [INFO ]  PROGRESS: at sentence #1910000, processed 20994697 words, keeping 472655 word types
2017-10-13 12:06:21,465 [MainThread  ] [INFO ]  PROGRESS: at sentence #1920000, processed 21129632 words, keeping 483234 word types
2017-10-13 12:06:21,609 [MainThread  ] [INFO ]  PROGRESS: at sentence #1930000, processed 21241099 words, keeping 484939 word types
2017-10-13 12:06:21,761 [MainThread  ] [INFO ]  PROGRESS: at sentence #1940000, processed 21360694 words, keeping 486726 word types
2017-10-13 12:06:21,915 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 21474656 words, keeping 488201 word types
2017-10-13 12:06:22,054 [MainThread  ] [INFO ]  PROGRESS: at sentence #19600

2017-10-13 12:06:35,568 [MainThread  ] [INFO ]  PROGRESS: at sentence #2520000, processed 27727349 words, keeping 580795 word types
2017-10-13 12:06:35,707 [MainThread  ] [INFO ]  PROGRESS: at sentence #2530000, processed 27833182 words, keeping 582434 word types
2017-10-13 12:06:35,848 [MainThread  ] [INFO ]  PROGRESS: at sentence #2540000, processed 27941401 words, keeping 584349 word types
2017-10-13 12:06:35,987 [MainThread  ] [INFO ]  PROGRESS: at sentence #2550000, processed 28051040 words, keeping 586012 word types
2017-10-13 12:06:36,134 [MainThread  ] [INFO ]  PROGRESS: at sentence #2560000, processed 28166192 words, keeping 587900 word types
2017-10-13 12:06:36,292 [MainThread  ] [INFO ]  PROGRESS: at sentence #2570000, processed 28282356 words, keeping 589201 word types
2017-10-13 12:06:36,440 [MainThread  ] [INFO ]  PROGRESS: at sentence #2580000, processed 28395935 words, keeping 590573 word types
2017-10-13 12:06:36,581 [MainThread  ] [INFO ]  PROGRESS: at sentence #25900

...

2017-10-13 17:44:50,706 [MainThread  ] [INFO ]  PROGRESS: at 54.43% examples, 153086 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:51,744 [MainThread  ] [INFO ]  PROGRESS: at 54.44% examples, 153086 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:52,777 [MainThread  ] [INFO ]  PROGRESS: at 54.44% examples, 153086 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:53,803 [MainThread  ] [INFO ]  PROGRESS: at 54.44% examples, 153086 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:54,813 [MainThread  ] [INFO ]  PROGRESS: at 54.45% examples, 153086 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:55,810 [MainThread  ] [INFO ]  PROGRESS: at 54.45% examples, 153086 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:56,826 [MainThread  ] [INFO ]  PROGRESS: at 54.45% examples, 153087 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:58,185 [MainThread  ] [INFO ]  PROGRESS: at 54.46% examples, 153083 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:59,194 [MainThread  ] [INFO ]  

2017-10-13 17:46:03,322 [MainThread  ] [INFO ]  PROGRESS: at 54.66% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:04,337 [MainThread  ] [INFO ]  PROGRESS: at 54.66% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:05,376 [MainThread  ] [INFO ]  PROGRESS: at 54.67% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:06,398 [MainThread  ] [INFO ]  PROGRESS: at 54.67% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:07,412 [MainThread  ] [INFO ]  PROGRESS: at 54.67% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:08,463 [MainThread  ] [INFO ]  PROGRESS: at 54.68% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:09,471 [MainThread  ] [INFO ]  PROGRESS: at 54.68% examples, 153085 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:10,647 [MainThread  ] [INFO ]  PROGRESS: at 54.68% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:11,657 [MainThread  ] [INFO ]  

2017-10-13 17:47:15,934 [MainThread  ] [INFO ]  PROGRESS: at 54.88% examples, 153079 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:16,971 [MainThread  ] [INFO ]  PROGRESS: at 54.89% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:47:18,135 [MainThread  ] [INFO ]  PROGRESS: at 54.89% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:47:19,199 [MainThread  ] [INFO ]  PROGRESS: at 54.90% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:20,203 [MainThread  ] [INFO ]  PROGRESS: at 54.90% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:21,303 [MainThread  ] [INFO ]  PROGRESS: at 54.90% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:22,319 [MainThread  ] [INFO ]  PROGRESS: at 54.91% examples, 153081 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:23,362 [MainThread  ] [INFO ]  PROGRESS: at 54.91% examples, 153082 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:47:24,407 [MainThread  ] [INFO ]  

2017-10-13 17:48:30,062 [MainThread  ] [INFO ]  PROGRESS: at 55.12% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:31,133 [MainThread  ] [INFO ]  PROGRESS: at 55.12% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:32,139 [MainThread  ] [INFO ]  PROGRESS: at 55.12% examples, 153082 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:33,141 [MainThread  ] [INFO ]  PROGRESS: at 55.13% examples, 153082 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:34,168 [MainThread  ] [INFO ]  PROGRESS: at 55.13% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:35,315 [MainThread  ] [INFO ]  PROGRESS: at 55.13% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:36,310 [MainThread  ] [INFO ]  PROGRESS: at 55.14% examples, 153081 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:37,471 [MainThread  ] [INFO ]  PROGRESS: at 55.14% examples, 153081 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:38,524 [MainThread  ] [INFO ]  

2017-10-13 17:49:43,067 [MainThread  ] [INFO ]  PROGRESS: at 55.34% examples, 153079 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:44,199 [MainThread  ] [INFO ]  PROGRESS: at 55.35% examples, 153079 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:49:45,225 [MainThread  ] [INFO ]  PROGRESS: at 55.35% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:46,251 [MainThread  ] [INFO ]  PROGRESS: at 55.35% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:49:47,305 [MainThread  ] [INFO ]  PROGRESS: at 55.36% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:48,308 [MainThread  ] [INFO ]  PROGRESS: at 55.36% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:49,322 [MainThread  ] [INFO ]  PROGRESS: at 55.36% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:50,381 [MainThread  ] [INFO ]  PROGRESS: at 55.37% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:51,420 [MainThread  ] [INFO ]  

In [ ]:
model.save('../data/lingvo/w2v_300_sg_10_w10')

In [9]:
class Sentences_phraser(object):
    def __init__(self, phraser):
        self.phraser = phraser
    def __iter__(self):
        for sent in self.phraser[iter_sents()]:
            yield sent

In [26]:
with GzipFile('../data/lingvo/trigram_corpus.txt.gz', 'w') as f:
    for sent in trigram_ph[iter_sents()]:
        f.write(unicode(' '.join(sent)).encode('utf8') + '\n')
        break

KeyboardInterrupt: 

In [25]:
print(unicode(' '.join(sent)).encode('utf8'))

вал планшайба секунда зубчатый_венец крепиться червячный_колесо


In [18]:
print(' '.join(sent))

вал планшайба секунда зубчатый_венец крепиться червячный_колесо


In [10]:
model = Word2Vec(trigram_ph[Sentences_phraser(trigram_ph)], size=dim, sg=1, 
                 min_count=5, window=10, workers=cpu_count)

2017-10-25 07:34:42,716 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-25 07:34:42,717 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2017-10-25 07:34:43,721 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 113858 words, keeping 13569 word types
2017-10-25 07:34:44,690 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 225483 words, keeping 22380 word types
2017-10-25 07:34:45,590 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 326531 words, keeping 30608 word types
2017-10-25 07:34:46,508 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 430515 words, keeping 39716 word types
2017-10-25 07:34:47,375 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 527838 words, keeping 45677 word types
2017-10-25 07:34:48,360 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 639470 words, keeping 53030 word types
2017-10-25 07:34:49,383 [MainThread  ]

2017-10-25 07:35:41,835 [MainThread  ] [INFO ]  PROGRESS: at sentence #630000, processed 6626137 words, keeping 323056 word types
2017-10-25 07:35:42,755 [MainThread  ] [INFO ]  PROGRESS: at sentence #640000, processed 6728370 words, keeping 328670 word types
2017-10-25 07:35:43,689 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 6833990 words, keeping 332649 word types
2017-10-25 07:35:44,602 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 6935887 words, keeping 336545 word types
2017-10-25 07:35:45,576 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7045297 words, keeping 339651 word types
2017-10-25 07:35:46,559 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7156996 words, keeping 343200 word types
2017-10-25 07:35:47,560 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 7270858 words, keeping 346544 word types
2017-10-25 07:35:48,541 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 7

2017-10-25 07:36:41,004 [MainThread  ] [INFO ]  PROGRESS: at sentence #1260000, processed 13207020 words, keeping 557293 word types
2017-10-25 07:36:41,988 [MainThread  ] [INFO ]  PROGRESS: at sentence #1270000, processed 13316572 words, keeping 560491 word types
2017-10-25 07:36:42,946 [MainThread  ] [INFO ]  PROGRESS: at sentence #1280000, processed 13424982 words, keeping 563859 word types
2017-10-25 07:36:43,919 [MainThread  ] [INFO ]  PROGRESS: at sentence #1290000, processed 13534258 words, keeping 566722 word types
2017-10-25 07:36:44,902 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 13641596 words, keeping 569733 word types
2017-10-25 07:36:45,833 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 13744300 words, keeping 573588 word types
2017-10-25 07:36:46,764 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 13844157 words, keeping 576992 word types
2017-10-25 07:36:47,736 [MainThread  ] [INFO ]  PROGRESS: at sentence #13300

2017-10-25 07:37:40,335 [MainThread  ] [INFO ]  PROGRESS: at sentence #1890000, processed 19795754 words, keeping 763983 word types
2017-10-25 07:37:41,215 [MainThread  ] [INFO ]  PROGRESS: at sentence #1900000, processed 19884586 words, keeping 766590 word types
2017-10-25 07:37:42,154 [MainThread  ] [INFO ]  PROGRESS: at sentence #1910000, processed 19986496 words, keeping 769985 word types
2017-10-25 07:37:43,117 [MainThread  ] [INFO ]  PROGRESS: at sentence #1920000, processed 20094067 words, keeping 772206 word types
2017-10-25 07:37:44,155 [MainThread  ] [INFO ]  PROGRESS: at sentence #1930000, processed 20210156 words, keeping 774963 word types
2017-10-25 07:37:45,052 [MainThread  ] [INFO ]  PROGRESS: at sentence #1940000, processed 20308237 words, keeping 777165 word types
2017-10-25 07:37:45,981 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 20410772 words, keeping 779801 word types
2017-10-25 07:37:46,906 [MainThread  ] [INFO ]  PROGRESS: at sentence #19600

2017-10-25 07:38:39,834 [MainThread  ] [INFO ]  PROGRESS: at sentence #2520000, processed 26364114 words, keeping 945315 word types
2017-10-25 07:38:40,784 [MainThread  ] [INFO ]  PROGRESS: at sentence #2530000, processed 26469294 words, keeping 947759 word types
2017-10-25 07:38:41,753 [MainThread  ] [INFO ]  PROGRESS: at sentence #2540000, processed 26578408 words, keeping 949771 word types
2017-10-25 07:38:42,738 [MainThread  ] [INFO ]  PROGRESS: at sentence #2550000, processed 26688664 words, keeping 953212 word types
2017-10-25 07:38:43,684 [MainThread  ] [INFO ]  PROGRESS: at sentence #2560000, processed 26792689 words, keeping 955616 word types
2017-10-25 07:38:44,658 [MainThread  ] [INFO ]  PROGRESS: at sentence #2570000, processed 26902682 words, keeping 957889 word types
2017-10-25 07:38:45,593 [MainThread  ] [INFO ]  PROGRESS: at sentence #2580000, processed 27006267 words, keeping 960122 word types
2017-10-25 07:38:46,510 [MainThread  ] [INFO ]  PROGRESS: at sentence #25900

...

2017-10-25 10:12:33,011 [MainThread  ] [INFO ]  PROGRESS: at sentence #91090000, processed 956248299 words, keeping 11198746 word types
2017-10-25 10:12:34,170 [MainThread  ] [INFO ]  PROGRESS: at sentence #91100000, processed 956353935 words, keeping 11199409 word types
2017-10-25 10:12:35,361 [MainThread  ] [INFO ]  PROGRESS: at sentence #91110000, processed 956464656 words, keeping 11200237 word types
2017-10-25 10:12:36,546 [MainThread  ] [INFO ]  PROGRESS: at sentence #91120000, processed 956572975 words, keeping 11201167 word types
2017-10-25 10:12:37,580 [MainThread  ] [INFO ]  PROGRESS: at sentence #91130000, processed 956661409 words, keeping 11202600 word types
2017-10-25 10:12:38,738 [MainThread  ] [INFO ]  PROGRESS: at sentence #91140000, processed 956769940 words, keeping 11203067 word types
2017-10-25 10:12:39,902 [MainThread  ] [INFO ]  PROGRESS: at sentence #91150000, processed 956877288 words, keeping 11204873 word types
2017-10-25 10:12:41,066 [MainThread  ] [INFO ]  

2017-10-25 10:13:42,867 [MainThread  ] [INFO ]  PROGRESS: at sentence #91700000, processed 962651907 words, keeping 11246888 word types
2017-10-25 10:13:43,955 [MainThread  ] [INFO ]  PROGRESS: at sentence #91710000, processed 962751091 words, keeping 11247612 word types
2017-10-25 10:13:45,083 [MainThread  ] [INFO ]  PROGRESS: at sentence #91720000, processed 962854764 words, keeping 11248228 word types
2017-10-25 10:13:46,257 [MainThread  ] [INFO ]  PROGRESS: at sentence #91730000, processed 962959640 words, keeping 11248620 word types
2017-10-25 10:13:47,377 [MainThread  ] [INFO ]  PROGRESS: at sentence #91740000, processed 963060580 words, keeping 11249610 word types
2017-10-25 10:13:48,576 [MainThread  ] [INFO ]  PROGRESS: at sentence #91750000, processed 963172112 words, keeping 11250547 word types
2017-10-25 10:13:49,733 [MainThread  ] [INFO ]  PROGRESS: at sentence #91760000, processed 963279403 words, keeping 11250929 word types
2017-10-25 10:13:50,857 [MainThread  ] [INFO ]  

2017-10-25 10:14:53,104 [MainThread  ] [INFO ]  PROGRESS: at sentence #92310000, processed 969072419 words, keeping 11298490 word types
2017-10-25 10:14:54,245 [MainThread  ] [INFO ]  PROGRESS: at sentence #92320000, processed 969177462 words, keeping 11298968 word types
2017-10-25 10:14:55,369 [MainThread  ] [INFO ]  PROGRESS: at sentence #92330000, processed 969280523 words, keeping 11299579 word types
2017-10-25 10:14:56,572 [MainThread  ] [INFO ]  PROGRESS: at sentence #92340000, processed 969393066 words, keeping 11300249 word types
2017-10-25 10:14:57,730 [MainThread  ] [INFO ]  PROGRESS: at sentence #92350000, processed 969500073 words, keeping 11300837 word types
2017-10-25 10:14:58,852 [MainThread  ] [INFO ]  PROGRESS: at sentence #92360000, processed 969602367 words, keeping 11301594 word types
2017-10-25 10:15:00,011 [MainThread  ] [INFO ]  PROGRESS: at sentence #92370000, processed 969709561 words, keeping 11302183 word types
2017-10-25 10:15:01,164 [MainThread  ] [INFO ]  

2017-10-25 10:16:03,338 [MainThread  ] [INFO ]  PROGRESS: at sentence #92920000, processed 975516101 words, keeping 11346494 word types
2017-10-25 10:16:04,504 [MainThread  ] [INFO ]  PROGRESS: at sentence #92930000, processed 975625433 words, keeping 11347220 word types
2017-10-25 10:16:05,653 [MainThread  ] [INFO ]  PROGRESS: at sentence #92940000, processed 975729114 words, keeping 11347700 word types
2017-10-25 10:16:06,803 [MainThread  ] [INFO ]  PROGRESS: at sentence #92950000, processed 975836909 words, keeping 11348335 word types
2017-10-25 10:16:07,945 [MainThread  ] [INFO ]  PROGRESS: at sentence #92960000, processed 975942778 words, keeping 11348966 word types
2017-10-25 10:16:09,075 [MainThread  ] [INFO ]  PROGRESS: at sentence #92970000, processed 976045760 words, keeping 11349644 word types
2017-10-25 10:16:10,233 [MainThread  ] [INFO ]  PROGRESS: at sentence #92980000, processed 976150844 words, keeping 11350422 word types
2017-10-25 10:16:11,409 [MainThread  ] [INFO ]  

2017-10-25 10:17:13,246 [MainThread  ] [INFO ]  PROGRESS: at sentence #93530000, processed 981902930 words, keeping 11395550 word types
2017-10-25 10:17:14,395 [MainThread  ] [INFO ]  PROGRESS: at sentence #93540000, processed 982008408 words, keeping 11396454 word types
2017-10-25 10:17:15,531 [MainThread  ] [INFO ]  PROGRESS: at sentence #93550000, processed 982113051 words, keeping 11396955 word types
2017-10-25 10:17:16,626 [MainThread  ] [INFO ]  PROGRESS: at sentence #93560000, processed 982213180 words, keeping 11397529 word types
2017-10-25 10:17:17,767 [MainThread  ] [INFO ]  PROGRESS: at sentence #93570000, processed 982319667 words, keeping 11398012 word types
2017-10-25 10:17:18,929 [MainThread  ] [INFO ]  PROGRESS: at sentence #93580000, processed 982427146 words, keeping 11398530 word types
2017-10-25 10:17:20,089 [MainThread  ] [INFO ]  PROGRESS: at sentence #93590000, processed 982535545 words, keeping 11399156 word types
2017-10-25 10:17:21,234 [MainThread  ] [INFO ]  

In [8]:
model.save('../data/lingvo/w2v_300_sg_5_w10_trigram')

2017-10-24 16:58:41,140 [MainThread  ] [INFO ]  saving Word2Vec object under ../data/lingvo/w2v_300_sg_5_w10_trigram, separately None
2017-10-24 16:58:41,141 [MainThread  ] [INFO ]  not storing attribute syn0norm
2017-10-24 16:58:41,142 [MainThread  ] [INFO ]  storing np array 'syn0' to ../data/lingvo/w2v_300_sg_5_w10_trigram.wv.syn0.npy
2017-10-24 16:58:59,723 [MainThread  ] [INFO ]  storing np array 'syn1neg' to ../data/lingvo/w2v_300_sg_5_w10_trigram.syn1neg.npy
2017-10-24 16:59:18,031 [MainThread  ] [INFO ]  not storing attribute cum_table
2017-10-24 16:59:46,558 [MainThread  ] [INFO ]  saved ../data/lingvo/w2v_300_sg_5_w10_trigram


In [34]:
!ls ../data/lingvo/w2v_300_sg_5_w10_trigram

ls: cannot access '../data/lingvo/w2v_300_sg_5_w10_trigram': No such file or directory


In [25]:
!ls -sh ../data/lingvo/w2v_300_sg_5_w10_trigram

241M ../data/lingvo/w2v_300_sg_5_w10_trigram


In [11]:
for w ,s in model.wv.most_similar(u'стол'):
    print('%s %s' % (w,s))

нпм 0.297611892223
выполпеп 0.277081847191
130g 0.268700033426
балаковский_аэс 0.257275521755
(125/25 0.256969988346
оранжевый_спектросмещать 0.253416627645
замена_к32е. 0.252790808678
сверхразведение_матричный 0.250886440277
цикло-(D-Val-NMeArg-Gly-Asp-Mamb(5-aca 0.249853163958
аэро_космоснимок 0.24928149581


# Save for Misha

In [5]:
trigram_ph = gensim.models.phrases.Phraser.load('../data/lingvo/trigram_ph')

2017-10-24 09:33:56,826 [MainThread  ] [INFO ]  loading Phraser object from ../data/lingvo/trigram_ph
2017-10-24 09:33:58,577 [MainThread  ] [INFO ]  loaded ../data/lingvo/trigram_ph


In [29]:
c = 0
l = []
for k,v in tqdm_notebook(trigram_ph.phrasegrams.items()):
    if v[0] > 10 and v[1] > 30:
        the_string = '_'.join(k)
        if re.search('[а-яА-Яa-zA-Z]', k[0]) and re.search('[а-яА-Яa-zA-Z]', k[1]):
            c+=1
            l.append([the_string, v[0], v[1]])
#         print('%s_%s %s' % (k[0], k[1], v))
        
df = pd.DataFrame(l)

In [ ]:
# df.sort_values(by=1, ascending=False)

In [30]:
len(df[0].unique())

1279338

In [34]:
with GzipFile('../data/collocations_bigram_all.txt.gz', 'w') as f:
    for tag in sorted(df[0].unique()):
        f.write(tag + '\n')

In [2]:
import xml.etree.ElementTree as ET

tree = ET.parse('../data/TestDocumentsResult.xml')
root = tree.getroot()

In [30]:
gold = {}
for child in root:
    sims = []
    for similars in child:
        for sim in similars:
            sims.append(sim.attrib['docId'])
    gold[child.attrib['docId']] = sims